In [33]:
# importing pandas, requests, os and json
import requests
import json
import pandas as pd
import os

# Foursquare

Send a request to Foursquare with a small radius (1000m) for all the bike stations in your city of choice. 

**Note:** I used Postman to explore the data in the json response.

In [39]:
def get_foursquare_data(api_key, bike_stations, radius=1000):
    '''
    Makes requests to the Foursquare API for each bike station in my city_bikes_Montreal.csv file.
    
    Args:
        api_key (str): The Foursquare API key.
        bike_stations (pd.DataFrame): A DataFrame containing bike station data.
        radius (int): The search radius in meters around each bike station. Defaults to 1000.

    Returns:
        list: A list of JSON responses from the Foursquare API for each bike station.
    '''
    
    base_url = "https://api.foursquare.com/v3/places/search"
    headers = {
        "accept": "application/json",
        "Authorization": api_key
                }
    responses = []

    for index, row in bike_stations.iterrows():
        url = f"{base_url}?ll={row['latitude']},{row['longitude']}&radius={radius}"
        response = requests.get(url, headers=headers)
        responses.append(response.json())

    return responses

# Path to CSV file
file_path = '../data/city_bikes_Montreal.csv'

# Read the CSV into a DataFrame
bike_stations = pd.read_csv(file_path)

# Foursquare API key
foursquare_key = os.environ.get('FOURSQUARE_API_KEY')

# Call the function
foursquare_responses = get_foursquare_data(foursquare_key, bike_stations)


In [40]:
print(foursquare_responses)

[{'results': [{'fsq_id': '4ff33b5fe4b0aeae9cc8fb6d', 'categories': [{'id': 10001, 'name': 'Amusement Park', 'short_name': 'Amusement Park', 'plural_name': 'Amusement Parks', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/arts_entertainment/themepark_', 'suffix': '.png'}}, {'id': 13018, 'name': 'Pub', 'short_name': 'Pub', 'plural_name': 'Pubs', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/nightlife/pub_', 'suffix': '.png'}}, {'id': 13065, 'name': 'Restaurant', 'short_name': 'Restaurant', 'plural_name': 'Restaurants', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/default_', 'suffix': '.png'}}], 'chains': [], 'closed_bucket': 'VeryLikelyOpen', 'distance': 145, 'geocodes': {'main': {'latitude': 45.516495, 'longitude': -73.565819}, 'roof': {'latitude': 45.516495, 'longitude': -73.565819}}, 'link': '/v3/places/4ff33b5fe4b0aeae9cc8fb6d', 'location': {'address': '2041 Saint-Denis Rue', 'country': 'CA', 'cross_street': '', 'formatted_address': '2041 S

Parse through the response to get the POI (such as restaurants, bars, etc) details you want (ratings, name, location, etc)

In [44]:
def foursquare_parse_response(foursquare_responses):
    '''
    Parses the Foursquare API responses to extract specific POI details.

    Args:
        foursquare_responses (list): A list of JSON responses from the Foursquare API.

    Returns:
        pd.DataFrame: A DataFrame containing the parsed POI data with specific columns.
    '''

    pois_list = []

    for response in foursquare_responses:
        for item in response.get('results', []):
            poi_info = {
                'name': item.get('name'),
                'category': item.get('categories', [{}])[0].get('name', 'N/A'),
                'address': item.get('location', {}).get('address', 'N/A'),
                'country': item.get('location', {}).get('country', 'N/A'),
                'latitude': item.get('geocodes', {}).get('main', {}).get('latitude'),
                'longitude': item.get('geocodes', {}).get('main', {}).get('longitude')
            }
            pois_list.append(poi_info)

    return pd.DataFrame(pois_list)

# Parse the responses
foursquare_parsed_data = foursquare_parse_response(foursquare_responses)

Put your parsed results into a DataFrame

In [45]:
foursquare_parsed_data

name        category  \
0                              Randolph Pub Ludique  Amusement Park   
1                                         Le 4e Mur     Music Venue   
2                           Patrick'S Pub Irlandais       Irish Pub   
3                                   Le Cheval Blanc             Bar   
4     Bibliothèque et Archives nationales du Québec         Library   
...                                             ...             ...   
1588                                        Nacarat    Cocktail Bar   
1589                               La Maison Simons  Clothing Store   
1590                                Nyks Bistro Pub             Bar   
1591                                   Cineplex Inc   Movie Theater   
1592                            Place des Festivals            Park   

                          address country   latitude  longitude  
0            2041 Saint-Denis Rue      CA  45.516495 -73.565819  
1            2021 Saint-Denis Rue      CA  45.516216 -73.565568  
2            1707 Saint-Denis Rue      CA  45.515508 -73.564043  
3               809 Ontario Rue E      CA  45.518170 -73.564467  
4     475 Blvd de Maisonneuve Est      CA  45.515487 -73.562251  
...                           ...     ...        ...        ...  
1588          900 René-Lévesque O      CA  45.500712 -73.568076  
1589   977 Sainte-Catherine Rue O      CA  45.501138 -73.572303  
1590           1250 Rue de Bleury      CA  45.506024 -73.566648  
1591   977 Sainte-Catherine Rue O      CA  45.501026 -73.572202  
1592                          N/A      CA  45.507086 -73.567505  

[1593 rows x 6 columns]

In [32]:
# Download the DataFrame to a CSV file for later use.

foursquare_parsed_data.to_csv('foursquare_data.csv', index=False)

# Yelp

Send a request to Yelp with a small radius (1000m) for all the bike stations in your city of choice. 

In [49]:
def get_yelp_data(api_key, bike_stations):
    '''
    Makes requests to the Yelp API for each bike station in my city_bikes_Montreal.csv file.

    Args:
        api_key (str): The Yelp API key.
        bike_stations (pd.DataFrame): A DataFrame containing bike station data.

    Returns:
        list: A list of JSON responses from the Yelp API for each bike station.
    '''
    
    base_url = "https://api.yelp.com/v3/businesses/search"
    headers = {
        "Authorization": f"Bearer {api_key}"
    }
    responses = []

    for index, row in bike_stations.iterrows():
        params = {
            'latitude': row['latitude'],
            'longitude': row['longitude'],
            'radius': 1000
            #'categories': 'restaurants, bars'
        }
        response = requests.get(base_url, headers=headers, params=params)
        responses.append(response.json())

    return responses

# Path to CSV file
file_path = '../data/city_bikes_Montreal.csv'

# Read the CSV into a DataFrame
bike_stations = pd.read_csv(file_path)

# Yelp API key
yelp_key = os.environ.get('yelp_api_key')

# Call the function
yelp_responses = get_yelp_data(yelp_key, bike_stations)

In [50]:
yelp_responses

[{'businesses': [{'id': '8NHV3DBvq9Q88ZtzdR6W2w',
    'alias': 'le-saint-bock-montréal-3',
    'name': 'Le Saint-Bock',
    'image_url': 'https://s3-media1.fl.yelpcdn.com/bphoto/CY_XIfn3yYa9cBhQz7F9YA/o.jpg',
    'is_closed': False,
    'url': 'https://www.yelp.com/biz/le-saint-bock-montr%C3%A9al-3?adjust_creative=BTBYgm9U7kHcGgsv_rxXnA&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_search&utm_source=BTBYgm9U7kHcGgsv_rxXnA',
    'review_count': 208,
    'categories': [{'alias': 'brasseries', 'title': 'Brasseries'}],
    'rating': 4.0,
    'coordinates': {'latitude': 45.5158203, 'longitude': -73.564641},
    'transactions': [],
    'price': '$$',
    'location': {'address1': '1749 Rue Saint-Denis',
     'address2': '',
     'address3': '',
     'city': 'Montreal',
     'zip_code': 'H2X 3K4',
     'country': 'CA',
     'state': 'QC',
     'display_address': ['1749 Rue Saint-Denis',
      'Montreal, QC H2X 3K4',
      'Canada']},
    'phone': '+15146808052',
    'display_phone': '+1 

Parse through the response to get the POI (such as restaurants, bars, etc) details you want (ratings, name, location, etc)

In [51]:
def parse_yelp_response(yelp_responses):
    '''
    Parses the Yelp API responses.

    Args:
        yelp_responses (list): A list of JSON responses from the Yelp API.

    Returns:
        pd.DataFrame: A DataFrame containing the parsed data.
    '''

    places_list = []

    for response in yelp_responses:
        businesses = response.get('businesses', [])
        for business in businesses:
            # Extracting the desired information including rating
            place_info = {
                'name': business.get('name'),
                'address': ', '.join(business['location'].get('display_address', [])),
                'category': ', '.join([category['title'] for category in business.get('categories', [])]),
                'latitude': business.get('coordinates', {}).get('latitude'),
                'longitude': business.get('coordinates', {}).get('longitude'),
                'rating': business.get('rating') 
            }
            places_list.append(place_info)

    return pd.DataFrame(places_list)

yelp_parsed_data = parse_yelp_response(yelp_responses)

Put your parsed results into a DataFrame

In [52]:
yelp_parsed_data

name  \
0             Le Saint-Bock   
1      Pizzeria Dei Compari   
2             Bouillon Bilk   
3              Poutineville   
4           Les Deux Gamins   
...                     ...   
3177          Bouillon Bilk   
3178                 Gokudo   
3179  Jérôme Ferrer Europea   
3180               Sansotei   
3181       Deville Dinerbar   

                                                address  \
0     1749 Rue Saint-Denis, Montreal, QC H2X 3K4, Ca...   
1     1668 Rue Saint-Denis, Montreal, QC H2X 3K6, Ca...   
2     1595 Boulevard Saint-Laurent, Montreal, QC H2X...   
3      1365 Rue Ontario E, Montreal, QC H2L 1S1, Canada   
4     170 Rue Prince Arthur E, Montreal, QC H2X 1B7,...   
...                                                 ...   
3177  1595 Boulevard Saint-Laurent, Montreal, QC H2X...   
3178     630 Rue Cathcart, Montreal, QC H3B 0C3, Canada   
3179  1065 Rue de la Montagne, Montreal, QC H3G 0B9,...   
3180  370 Rue Sainte-Catherine O, Montreal, QC H3B 1...   
3181     1425 Rue Stanley, Montreal, QC H3A 1P4, Canada   

                                  category   latitude  longitude  rating  
0                               Brasseries  45.515820 -73.564641     4.0  
1                                    Pizza  45.515000 -73.563750     4.0  
2                          Modern European  45.511040 -73.565800     4.5  
3                              Poutineries  45.523205 -73.561300     4.5  
4         French, Wine Bars, Cocktail Bars  45.515450 -73.570950     4.0  
...                                    ...        ...        ...     ...  
3177                       Modern European  45.511040 -73.565800     4.5  
3178  Cocktail Bars, Japanese, Speakeasies  45.503030 -73.568380     4.5  
3179                                French  45.496475 -73.571785     4.5  
3180           Beer, Wine & Spirits, Ramen  45.505610 -73.567120     4.5  
3181                                Diners  45.499686 -73.574147     4.0  

[3182 rows x 6 columns]

# Comparing Results

Which API provided you with more complete data? Provide an explanation. 

I prefer the Foursquare API because the documentation was easier to understand. But it was easier for me to get the rating from the Yelp API. With that said, I believe the Yelp API gave me better quality data.

Get the top 10 restaurants according to their rating

In [54]:
# Sorts the data based on the rating column
yelp_sorted = yelp_parsed_data.sort_values(by='rating', ascending=False)

# show only the top 10
top_10 = yelp_sorted.head(10)

In [55]:
top_10

name  \
2599  Crèmerie Chateaubriand   
340   Beigne la Bonne Humeur   
1058            Café Barista   
2410            Arrêt de Bus   
139               Doña María   
140          Banh Mi Co Kieu   
1312            Arrêt de Bus   
2415                   Phafo   
2417             Parc Morgan   
150                  La Prep   

                                                address  \
2599  740 Boulevard Crémazie E, Montreal, QC H2P 1G2...   
340   3257 Rue Beaubien E, Montréal-Est, QC H1X 1G4,...   
1058  111A Rue de Louvain O, Montreal, QC H2N 1A3, C...   
2410  4731 Sainte-Catherine E, Montreal, QC H1V 1Z3,...   
139   2489 Rue Jean Talon E, Montreal, QC H2E 1W3, C...   
140   2569 Rue Jean-Talon, Montreal, QC H2A 1T8, Canada   
1312  4731 Sainte-Catherine E, Montreal, QC H1V 1Z3,...   
2415  4456 Rue Sainte-Catherine E, Montreal, QC H1V ...   
2417          Rue Gaboury, Montreal, QC H1V 2L7, Canada   
150    433 Rue Chabanel W, Montreal, QC H2N 2J4, Canada   

                                   category   latitude  longitude  rating  
2599              Ice Cream & Frozen Yogurt  45.548190 -73.635700     5.0  
340          Bakeries, Coffee & Tea, Donuts  45.555329 -73.586255     5.0  
1058                      Coffee Roasteries  45.542997 -73.656485     5.0  
2410                                 French  45.554862 -73.531440     5.0  
139                              Salvadoran  45.553620 -73.602420     5.0  
140                              Vietnamese  45.554644 -73.601414     5.0  
1312                                 French  45.554862 -73.531440     5.0  
2415        Food Delivery Services, Haitian  45.552200 -73.532830     5.0  
2417                                  Parks  45.551173 -73.532426     5.0  
150   Breakfast & Brunch, Sandwiches, Salad  45.538759 -73.654602     5.0

In [56]:
# Download the DataFrame to a CSV file for later use.

yelp_parsed_data.to_csv('yelp_data.csv', index=False)